In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import numpy as np
import pandas as pd
import torch
import argparse
from models.data_process import get_datatensor_partitions, prepare_nonproto_features, generate_partition_datatensor,get_data_ready
from models.dataset import ProtospacerDataset, ProtospacerExtendedDataset
from models.trainval_workflow import run_trainevaltest_workflow
from models.trainval_workflow import run_inference
from models.hyperparam import build_config_map
from src.utils import create_directory, one_hot_encode, get_device, ReaderWriter 
from src.utils import print_eval_results, plot_y_distrib_acrossfolds, compute_eval_results_df
import matplotlib.pyplot as plt

In [3]:
cmd_opt = argparse.ArgumentParser(description='Argparser for data')
cmd_opt.add_argument('-model_name',  type=str, help = 'name of the model')
cmd_opt.add_argument('-exp_name',  type=str, help = 'name of the experiment')

cmd_opt.add_argument('-data_dir',  type=str,default = './data/', help = 'directory of the data')
cmd_opt.add_argument('-target_dir',  type=str, default='processed',  help = 'folder name to save the processed data')
cmd_opt.add_argument('-working_dir',  type=str, default='./', help = 'the main working directory')
cmd_opt.add_argument('-output_path', type=str, help='path to save the trained model')
cmd_opt.add_argument('-random_seed', type=int,default=42)
cmd_opt.add_argument('-epoch_num', type=int, default =200, help='number of training epochs')
args, _ = cmd_opt.parse_known_args()

### Functions to make data ready and get predefined hyperparams for a given model and experiment choice

In [4]:
# predefined hyperparameters depending on the chosen model and experiment
def get_hyperparam_config(args):
    "return predefined hyperparameters for each model"
    to_gpu = True
    gpu_index=0
    optim_tup = None
    
    if args.model_name == 'FFN':
        batch_size = 100
        num_epochs = 300
        h = [60,10]
        l2_reg =0.1
        model_config_tup = (h, l2_reg, batch_size, num_epochs)
        
        if args.exp_name == 'protospacer_extended':
            mlpembedder_tup = (10, 16, 2, torch.nn.ReLU, 0.1, 1)
            xproto_inputsize = 20 + 10
        else:
            mlpembedder_tup = None
            xproto_inputsize = 20
        
        loss_func_name = 'MSEloss'
        perfmetric_name = 'pearson'
        
    if args.model_name == 'CNN':
        k = 2
        l2_reg = 0.5
        batch_size = 100
        num_epochs = 300
        model_config_tup = (k, l2_reg, batch_size, num_epochs)


        # input_dim, embed_dim, mlp_embed_factor, nonlin_func, p_dropout, num_encoder_units
        if args.exp_name == 'protospacer_extended':
            mlpembedder_tup = (10, 16, 2, torch.nn.ReLU, 0.1, 1)
            xproto_inputsize = 20 + 10
        else:
            mlpembedder_tup = None
            xproto_inputsize = 20

        loss_func_name = 'MSEloss'
        # loss_func_name = 'SmoothL1loss'
        perfmetric_name = 'spearman'

    elif args.model_name == 'RNN':
        embed_dim = 64
        hidden_dim = 64
        z_dim = 32
        num_hidden_layers =2
        bidirection = True
        p_dropout = 0.1     
        rnn_class = torch.nn.GRU
        nonlin_func = torch.nn.ReLU
        pooling_mode = 'none'
        l2_reg = 1e-5
        batch_size = 1500
        num_epochs = 500

        model_config_tup = (embed_dim, hidden_dim, z_dim, num_hidden_layers, bidirection, 
                   p_dropout, rnn_class, nonlin_func, pooling_mode, l2_reg, batch_size, num_epochs)

        # input_dim, embed_dim, mlp_embed_factor, nonlin_func, p_dropout, num_encoder_units
        if args.exp_name == 'protospacer_extended':
            mlpembedder_tup = (10, 16, 2, torch.nn.ReLU, 0.1, 1)
            xproto_inputsize = 20 + 10
        else:
            mlpembedder_tup = None
            xproto_inputsize = 20

        loss_func_name = 'SmoothL1loss'
        perfmetric_name = 'pearson'

    elif args.model_name == 'Transformer':
        embed_dim = 128
        num_attn_heads = 4
        num_trf_units = 1
        pdropout = 0.1
        activ_func = torch.nn.GELU
        multp_factor = 2
        multihead_type = 'Wide'
        pos_embed_concat_opt = 'stack'
        pooling_opt = 'none'
        weight_decay = 1e-8
        batch_size = 1000
        num_epochs = 1000


        model_config_tup = (embed_dim, num_attn_heads, num_trf_units,
                            pdropout, activ_func, multp_factor, multihead_type, 
                            pos_embed_concat_opt, pooling_opt, weight_decay, batch_size, num_epochs)

        # input_dim, embed_dim, mlp_embed_factor, nonlin_func, p_dropout, num_encoder_units
        if args.exp_name == 'protospacer_extended':
            mlpembedder_tup = (10, 16, 2, torch.nn.GELU, 0.1, 1)
            xproto_inputsize = 20 + 10
        else:
            mlpembedder_tup = None
            xproto_inputsize = 20 

        loss_func_name = 'SmoothL1loss'
        perfmetric_name = 'pearson'


    mconfig, options = build_config_map(args.model_name, 
                                        optim_tup, 
                                        model_config_tup, 
                                        mlpembedder_tup, 
                                        loss_func = loss_func_name)



    options['input_size'] = xproto_inputsize
    options['loss_func'] = loss_func_name # to refactor
    options['model_name'] = args.model_name
    options['perfmetric_name'] = perfmetric_name
    return mconfig, options

#import os
#os.environ['CUDA_LAUNCH_BLOCKING'] = '1'


### Run training workflow for nerural network models

In [ ]:
dsettypes = ['train', 'validation','test']
gpu_index = 0
res_desc = {}
version=2
for model_name in [ 'RNN']:  #'FFN','CNN', 'RNN',Transformer
    print(model_name)
    args.model_name =  model_name # {'RNN','CNN', 'Transformer'}
    res_desc[model_name] = {}
    for exp_name in ['protospacer','protospacer_extended']:
        args.exp_name = exp_name
        model_path = os.path.join(args.working_dir, 
                                  'output', 
                                  f'{model_name}_v{version}',
                                  exp_name)
        dpartitions, datatensor_partitions = get_data_ready(args, 
                                                            normalize_opt='max',
                                                            train_size=0.9, 
                                                            fdtype=torch.float32,
                                                            plot_y_distrib=False)
        mconfig, options = get_hyperparam_config(args)
        print(options)
        
#         options['num_epochs'] = 10 # use this if you want to test a whole workflow run for all models using 10 epochs
        
        perfmetric_name = options['perfmetric_name']
        train_val_path = os.path.join(model_path, 'train_val')
        test_path = os.path.join(model_path, 'test')
        
        print(f'Running model: {model_name}, exp_name: {exp_name}, saved at {train_val_path}')
        perfmetric_run_map, score_run_dict = run_trainevaltest_workflow(datatensor_partitions, 
                                                                        (mconfig, options), 
                                                                        train_val_path,
                                                                        dsettypes,
                                                                        perfmetric_name,
                                                                        gpu_index, 
                                                                        to_gpu=True)
        print('='*15)
        res_desc[model_name][exp_name] = compute_eval_results_df(train_val_path, len(dpartitions))        

RNN
--- max normalization ---
{'run_num': -1, 'num_epochs': 500, 'weight_decay': 1e-05, 'fdtype': torch.float32, 'to_gpu': True, 'loss_func': 'SmoothL1loss', 'input_size': 20, 'model_name': 'RNN', 'perfmetric_name': 'pearson'}
Running model: RNN, exp_name: protospacer, saved at ./output/RNN_v2/protospacer/train_val
cuda:0
validation
test
number of epochs 500


/home/ubuntu/anaconda3/envs/graphnn/lib/python3.9/site-packages/torch/cuda/__init__.py:546: UserWarning: Can't initialize NVML
  warnings.warn("Can't initialize NVML")


weight_decay 1e-05
Epoch: 0
Regression report on all events:
MAE:
8.573200753584869
MSE:
160.005895271107
Correlation coefficient:
-0.044810954352089254
Spearman coefficient:
-0.0397752220421249
Pearson coefficient:
-0.04481095435208927
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 0
Regression report on all events:
MAE:
8.206355693058734
MSE:
148.25282092334433
Correlation coefficient:
-0.12734100308361826
Spearman coefficient:
-0.1702726804053275
Pearson coefficient:
-0.12734100308361826
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 0
Regression report on all events:
MAE:
8.429215416533395
MSE:
163.81096421741663
Correlation coefficient:
-0.16989568942712596
Spearman coefficient:
-0.2059809539292696
Pearson coefficient:
-0.16989568942712596
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 1
Regression report on all events:
MAE:
8.08789625542915
MSE:
150.3037387007741
Correlation coefficient:
-0.03406141629111619
Spearman coefficie

Epoch: 10
Regression report on all events:
MAE:
6.045482629257741
MSE:
93.27290295536318
Correlation coefficient:
0.2979930195999198
Spearman coefficient:
0.33986024848315943
Pearson coefficient:
0.29799301959991975
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 10
Regression report on all events:
MAE:
5.8049480664400965
MSE:
85.46539123345376
Correlation coefficient:
0.27973754233316833
Spearman coefficient:
0.3519506701875329
Pearson coefficient:
0.2797375423331684
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 10
Regression report on all events:
MAE:
6.132094551614459
MSE:
97.19534325716174
Correlation coefficient:
0.3131963153556856
Spearman coefficient:
0.3447824618477219
Pearson coefficient:
0.31319631535568554
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 11
Regression report on all events:
MAE:
6.0158323484619585
MSE:
89.6839741778998
Correlation coefficient:
0.30144848066264907
Spearman coefficient:
0.3439097673274281
Pear

Epoch: 19
Regression report on all events:
MAE:
5.415813913418649
MSE:
72.97589256648138
Correlation coefficient:
0.5183722987068411
Spearman coefficient:
0.5486333297424274
Pearson coefficient:
0.5183722987068414
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 19
Regression report on all events:
MAE:
5.215306820331907
MSE:
66.79840510334364
Correlation coefficient:
0.5176106777764133
Spearman coefficient:
0.5652377935767602
Pearson coefficient:
0.5176106777764136
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 19
Regression report on all events:
MAE:
5.532778760410984
MSE:
76.94547122977627
Correlation coefficient:
0.5261121764412805
Spearman coefficient:
0.5386998862132749
Pearson coefficient:
0.5261121764412806
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch 20/500, Training Loss: 4.9443, Validation Loss: 4.7396, Test loss: 5.0597
Epoch 20/500, best pearson corr. so far: 0.5176
~~~~~~~~~~~~~~~~~~~~~~~~~
Epoch: 20
Regression report on

...

Epoch: 478
Regression report on all events:
MAE:
0.8372766527934501
MSE:
1.618577899243686
Correlation coefficient:
0.9909067303532467
Spearman coefficient:
0.9801557409490029
Pearson coefficient:
0.9909067303532464
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 478
Regression report on all events:
MAE:
4.032119831595958
MSE:
33.87476969000624
Correlation coefficient:
0.7914125713289917
Spearman coefficient:
0.7329140480446206
Pearson coefficient:
0.7914125713289916
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 478
Regression report on all events:
MAE:
4.082368020101709
MSE:
34.32448762459977
Correlation coefficient:
0.7719656494319193
Spearman coefficient:
0.7329988255055149
Pearson coefficient:
0.7719656494319187
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 479
Regression report on all events:
MAE:
0.8292840384886471
MSE:
1.5753518710851355
Correlation coefficient:
0.9911336712506613
Spearman coefficient:
0.9803921693856019
Pea

Epoch: 488
Regression report on all events:
MAE:
0.8159836625638427
MSE:
1.560824903155507
Correlation coefficient:
0.9912424257849343
Spearman coefficient:
0.9814153889254883
Pearson coefficient:
0.9912424257849345
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 488
Regression report on all events:
MAE:
4.032476046057475
MSE:
33.55602696101523
Correlation coefficient:
0.7943513081448378
Spearman coefficient:
0.7335980039877303
Pearson coefficient:
0.7943513081448377
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 488
Regression report on all events:
MAE:
4.116777821086617
MSE:
34.51026866640336
Correlation coefficient:
0.7712853073943824
Spearman coefficient:
0.7336132150218072
Pearson coefficient:
0.7712853073943823
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 489
Regression report on all events:
MAE:
0.7991225460598825
MSE:
1.4991828421921316
Correlation coefficient:
0.9915821607995605
Spearman coefficient:
0.9817022029885978
Pea

Epoch: 498
Regression report on all events:
MAE:
0.7954987521742324
MSE:
1.4625113831833938
Correlation coefficient:
0.9917960009166793
Spearman coefficient:
0.9814229231062584
Pearson coefficient:
0.9917960009166792
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 498
Regression report on all events:
MAE:
4.059237086825484
MSE:
34.0508122460689
Correlation coefficient:
0.7919658537706223
Spearman coefficient:
0.7339841959381033
Pearson coefficient:
0.7919658537706222
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 498
Regression report on all events:
MAE:
4.136799602020784
MSE:
34.77386300173467
Correlation coefficient:
0.7704070132215337
Spearman coefficient:
0.734140551124128
Pearson coefficient:
0.7704070132215334
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 499
Regression report on all events:
MAE:
0.7885544497415616
MSE:
1.4298183847299926
Correlation coefficient:
0.9919698576986288
Spearman coefficient:
0.981549828667601
Pears

Epoch: 7
Regression report on all events:
MAE:
6.085026857515399
MSE:
90.26258391005132
Correlation coefficient:
0.2874900236812612
Spearman coefficient:
0.3358834964311207
Pearson coefficient:
0.2874900236812612
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 7
Regression report on all events:
MAE:
6.454786518577249
MSE:
101.78162036247964
Correlation coefficient:
0.3420765157957474
Spearman coefficient:
0.3894190547673607
Pearson coefficient:
0.3420765157957473
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 7
Regression report on all events:
MAE:
6.340210300437269
MSE:
100.2528909511808
Correlation coefficient:
0.28711887600874225
Spearman coefficient:
0.34034090737517025
Pearson coefficient:
0.2871188760087422
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 8
Regression report on all events:
MAE:
6.039572990477471
MSE:
90.42196947032387
Correlation coefficient:
0.27196866889880417
Spearman coefficient:
0.3235812501236952
Pearson co

Epoch: 17
Regression report on all events:
MAE:
5.547208631848732
MSE:
76.61493423831502
Correlation coefficient:
0.46490987484247226
Spearman coefficient:
0.49313269697072243
Pearson coefficient:
0.46490987484247237
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 17
Regression report on all events:
MAE:
5.761274339090211
MSE:
84.30882200710688
Correlation coefficient:
0.5267160593351389
Spearman coefficient:
0.5667745481756904
Pearson coefficient:
0.526716059335139
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch: 17
Regression report on all events:
MAE:
5.756456238922202
MSE:
85.58371958856368
Correlation coefficient:
0.4652114098301779
Spearman coefficient:
0.5077219684074245
Pearson coefficient:
0.4652114098301777
------------------------------

xxxxxxxxxxxxxxxxxxxxxxxxx
Epoch 18/500, Training Loss: 5.0716, Validation Loss: 5.2874, Test loss: 5.2845
Epoch 18/500, best pearson corr. so far: 0.5267
~~~~~~~~~~~~~~~~~~~~~~~~~
Epoch: 18
Regression report 